# Assignment 5: Neuroevolution

**Goal**: Implement an Evolutionary Algorithm to optimize an Artificial Neural Network (ANN) based controller for the CartPole task in OpenAI Gym environment.

CartPole evaluation environment functions are provided. Your goal is to implement your ANN to control the cartpole and use your Evolutionary Algorithm to optimize the ANN parameters (weights).

Please answer the `Questions` and implement coding `Tasks` by filling **PLEASE FILL IN** sections. *Documentation* of your code is also important. You can find the grading scheme in implementation cells.

  * Plagiarism is automatically checked and set to **0 points**

  * It is allowed to learn from external resources but copying is not allowed. If you use any external resource, please cite them in the comments (e.g. `# source: https://...../` (see `fitness_function`))

**Install Prerequisites**

In [7]:
# Run this cell to install the required libraries
# %pip install numpy matplotlib scipy

**Imports**

In [8]:
# Necessary libraries
import matplotlib.pyplot as plt
import numpy as np


In [9]:
# Enables inline matplotib graphs
%matplotlib inline
# Comment the line above and uncomment the lines below to have interactive plots
# WARN: may cause dependency issues
# %matplotlib qt5
# %pip install PyQt5
# plt.ion()

In [10]:
# %pip install gymnasium
import gymnasium as gym

---
**Question 1 (0-0.25-0.5 pt):** Following link provides more information about the CartPole environemnt we would like to find an ANN to control: https://www.gymlibrary.dev/environments/classic_control/cart_pole/

Please have a look at the link and note the observation and action spaces, how many dimensions they have? Are they continous or discrete, and what kinds of value they can get?

**Answer:** Observation spaces have ```4``` continuous dimensions, which are "Cart Position", "Cart Velocity", "Pole Angle" and "Pole Angular Velocity". "Cart Position" has value from ```-4.8``` to ```4.8```; "Cart Velocity" has no bounds; "Pole Angle" has value from ```-0.418 (-24°)``` to ```0.418 (24°)```; "Pole Angular Velocity" has no bounds.
Action spaces have ```2``` discrete dimensions with values of ```0 (Push cart to the left)``` and ```1 (Push cart to the right)```.

---
**Question 2 (0-0.25-0.5 pt):** What is your proposed ANN architecture and why? Please also discuss the activation functions you choose.

**Answer:** PLEASE FILL IN

---
**Task 1: Implementation of Evolutionary Algrotihm (0-1.6-3.8-4.2-5 pt):** Implement your evolutionary algorithm to find an ANN controller for the CartPole task.

In [11]:
#################################
# Grading
# 0 pts if the code does not work, code works but it is fundamentally incorrect
# 1.6 pts if the code works but some functions are incorrect and it is badly explained
# 3.8 pts if the code works but some functions are incorrect but it is explained well
# 4.2 pts if the code works very well aligned with the task without any mistakes, but it is badly explained
# 5 pts if the code works very well aligned with the task without any mistakes, and it is well explained
################################################################

import torch
import numpy as np
# Artificial Neural Network parameters (weights)
# See here: https://www.gymlibrary.dev/environments/classic_control/cart_pole/ for input and output space
# PLEASE SPECIFY BELOW
inp = 4  # Cart Position, Cart Velocity, Pole Angle, Pole Angular Velocity
hid = 10  
out = 1  # action: left or right
###################
# Define the ANN structure
class ANN:
    def __init__(self, inp, hid, out):
        self.inp = inp
        self.hid = hid
        self.out = out
        self.weights1 = np.random.randn(self.inp, self.hid)
        self.weights2 = np.random.randn(self.hid, self.out)
        self.bias1 = np.random.randn(self.hid)
        self.bias2 = np.random.randn(self.out)

    def forward(self, x):
        self.z1 = np.dot(x, self.weights1) + self.bias1
        self.a1 = self.tanh(self.z1)
        self.z2 = np.dot(self.a1, self.weights2) + self.bias2
        self.a2 = self.tanh(self.z2)
        return self.a2

    def tanh(self, s):
        return 1 / (1 + np.exp(-s))

#Open AI gym environment
env = gym.make("CartPole-v1")

# CartPole evaluation function
def cartpole(x):
    ann = ANN(inp, hid, out)
    ann.weights1 = x[:inp*hid].reshape(inp, hid) # Extract inp*hid weights from x and reshape to (inp, hid)
    ann.weights2 = x[inp*hid:inp*hid+hid*out].reshape(hid, out)
    ann.bias1 = x[inp*hid+hid*out:inp*hid+hid*out+hid] # Extract hid biases from x
    ann.bias2 = x[-out:] # Extract last out biases from x

    # Reset environment
    observation, info = env.reset(seed=0)

    rew = 0  # Initial reward
    step = 0  # step counter
    done = False
    maxStep = 1000  # maximum number of steps
    while not done and step < 1000:  # run nStep number of time
        action_prob = ann.forward(observation)
        action = 0 if action_prob < 0 else 1  # 负值输出0，正值输出1

        # 动作应基于人工神经网络的输出
        observation, reward, done, tr, info = env.step(action)
        step += 1  # 步数计数器
        rew = rew + reward  # 每步增加奖励

        # 检查观测值是否超出阈值
        cart_position, cart_velocity, pole_angle, pole_angular_velocity = observation
        if abs(cart_position) > 4.8 or abs(pole_angle) > 0.418:
            done = True
        print(f"Step: {step}, Observation: {observation}, Action: {action}, Reward: {reward}, Total Reward: {rew}")

    env.close()
    return np.minimum(maxStep, rew)  # return the reward or maxStep (if maxStep < 1000, this means that pole fell)



# CartPole evaluation function with video recording
def cartpole_record_video(x):
    tmp_env = gym.make("CartPole-v1", render_mode="rgb_array")

    # Video recording function - be sure to check the folder path - you should see the video here:content/video/cartpole
    env = gym.wrappers.RecordVideo(env=tmp_env, video_folder="content/video/cartpole", name_prefix="cartpole")

    ann = ANN(inp, hid, out)
    ann.weights1 = x[:inp*hid].reshape(inp, hid)
    ann.weights2 = x[inp*hid:inp*hid+hid*out].reshape(hid, out)
    ann.bias1 = x[inp*hid+hid*out:inp*hid+hid*out+hid]
    ann.bias2 = x[-out:]

    # Reset environment
    observation, info = env.reset(seed=0)

    rew = 0  # Initial reward
    step = 0  # step counter
    done = False
    maxStep = 1000  # maximum number of steps
    while not done and step < 1000:  # run nStep number of time
        action_prob = ann.forward(observation)
        action = 0 if action_prob < 0.5 else 1

        # action should be provided based on the output of the artificial neural network
        observation, reward, done, tr, info = env.step(action)
        step += 1  # step counter
        rew = rew + reward  # after each step increment reward
        env.render()

    env.close_video_recorder()
    env.close()
    return np.minimum(maxStep, rew)  # return the reward or maxStep (if maxStep < 1000, this means that pole fell)




# CartPole evaluation function for visualizing the cartpole environment
def cartpole_visualize(x):
    tmp_env = gym.make("CartPole-v1", render_mode="human")

    ann = ANN(inp, hid, out)
    ann.weights1 = x[:inp*hid].reshape(inp, hid)
    ann.weights2 = x[inp*hid:inp*hid+hid*out].reshape(hid, out)
    ann.bias1 = x[inp*hid+hid*out:inp*hid+hid*out+hid]
    ann.bias2 = x[-out:]

    # Reset environment
    observation, info = tmp_env.reset(seed=0)

    rew = 0  # Initial reward
    step = 0  # step counter
    done = False
    maxStep = 1000  # maximum number of steps
    while not done and step < 1000:  # run nStep number of time
        action_prob = ann.forward(observation)
        action = 0 if action_prob < 0.5 else 1

        # action should be provided based on the output of the artificial neural network
        observation, reward, done, tr, info = tmp_env.step(action)
        step += 1  # step counter
        rew = rew + reward  # after each step increment reward
        tmp_env.render()

    tmp_env.close()
    return np.minimum(maxStep, rew)  # return the reward or maxStep (if maxStep < 1000, this means that pole fell)


def initialization(population_size, num_dimensions):
    """
    Initialize the starting population with random individuals.
    Each gene of an individual corresponds to the weights and offsets of an ANN.
    """
    # Create an initial population of size (population_size, num_dimensions), row is an individual, column is a dimension(gene).
    x = np.random.uniform(
        low=-1, high=1, size=(population_size, num_dimensions)
    )
    return x  # Return population


def evaluation(x, objective_function):
    """Evaluate the fitness of the population members."""
    return fitness


def crossover(x_parents, p_crossover):
    """Perform crossover to create offsprings."""
    offspring = []
    n_parents = x_parents.shape[0]
    n_dimension = x_parents.shape[1]

    for _ in range(n_parents // 2):
        # Randomly select two parents
        parents_indices = np.random.choice(range(n_parents), size=2, replace=False)

        if np.random.rand() < p_crossover:
            # Exchange genes at a random crossover point
            crossover_point = np.random.randint(1, n_dimension)

            # Create offspring by combining genes from selected parents
            parent1 = x_parents[parents_indices[0]]
            parent2 = x_parents[parents_indices[1]]
            # Perform crossover, the first child gets the first part of parent1 and the second part of parent2, and vice versa
            child1 = np.hstack((parent1[:crossover_point], parent2[crossover_point:]))
            child2 = np.hstack((parent2[:crossover_point], parent1[crossover_point:]))

            offspring.append(child1)
            offspring.append(child2)
        else:
            # If no crossover was done, just pass parents to the next generation
            offspring.extend(x_parents[parents_indices])

    return np.array(offspring)


def mutation(x, m_rate):
    """Apply mutation to an individual."""
    for _ in range(len(x)):
        if np.random.rand() < m_rate:

            # Randomly select a gene to mutate
            gene_idx = np.random.randint(len(x))

            # Mutate the selected gene with a random value within the boundaries
            x[gene_idx] = np.random.uniform(-1, 1)
    return x


def parent_selection(x, f):
    """Select parents for the next generation
        Two methods can be used: select the best individual or randomly select individuals for the tournament.
    """
    tournament_size = 3  # Number of individuals participating in the tournament, the best one/a random one will be selected
    x_parents = []
    f_parents = []

    # Assume the population size of parents is the same as the population size of the current generation
    while len(x_parents) < len(x):
        indices = np.random.choice(range(len(x)), size=tournament_size, replace=False)

        # Select randomly
        # parents_idx = np.random.choice(indices)
        
        # Append the best individual to the parents
        parents_idx = indices[np.argmin(f[indices])]
        
        x_parents.append(x[parents_idx])
        f_parents.append(f[parents_idx])

    return np.array(x_parents), np.array(f_parents)


def survivor_selection(x, f, x_offspring, f_offspring):
    """Select the survivors, for the population of the next generation"""
    # x and x_offspring are (population_size, num_dimensions) arrays, f and f_offspring are 1D arrays
    combined_population = np.vstack((x, x_offspring))
    combined_fitness = np.hstack((f, f_offspring))

    # Convert fitness values to probabilities
    fitness_probabilities = 1.0 / combined_fitness
    fitness_probabilities /= np.sum(fitness_probabilities)

    # Select individuals randomly based on their fitness probabilities (Roulette Wheel Selection)
    survivors_idx = np.random.choice(
        range(len(combined_fitness)),
        size=len(x),
        replace=False,
        p=fitness_probabilities,
    )
    
    # Selct the best individuals
    # survivors_idx = np.argsort(combined_fitness)[:len(x)]

    x = combined_population[survivors_idx]
    f = combined_fitness[survivors_idx]

    return x, f

# Implement your Evolutionary Algorithm to find the ANN weigths that can balance the CartPole
# Feel free to add any functions, such as initialization, crossover, etc.. to make it work!
def ea(
    # hyperparameters of the algorithm
    population_size,
    max_fit_evals,  # Maximum number of evaluations
    p_crossover,  # Probability of performing crossover operator
    m_rate,  # mutation rate
    objective_function,  # objective function to be minimized
    dimensions=inp * hid + hid + hid * out + out,  # number of dimensions
):
    """
    Methodology: Record the best individual in each generation, either the best in its parent generation or a new offspring.
    """
    # Initialize population
    x = initialization(population_size, dimensions)
    f = evaluation(x, objective_function)

    # Calculate the maximum number of generations
    max_generations = int(max_fit_evals / population_size)

    # Find the best individual and append to a list to keep track in each generation
    idx = np.argmin(f)
    x_best = [x[idx]]
    f_best = [f[idx]]

    # Loop over the generations
    for _ in range(max_generations - 1):
        # Perform the EA steps
        ################################################################
        # Select parents
        x_parents = parent_selection(x, f)[0]

        # Generate offsprings through crossover
        x_offspring = crossover(x_parents, p_crossover)
        # Apply mutation
        for individual in x_offspring:
            mutation(individual, m_rate)

        # Evaluate offsprings
        f_offspring = evaluation(x_offspring, objective_function)
        # Select survivors
        x, f = survivor_selection(x, f, x_offspring, f_offspring)

        ################################################################
        # Find the best individual in current generation and add to the list
        idx = np.argmin(f)
        xi_best = x[idx]
        fi_best = f[idx]
        if fi_best < f_best[-1]:
            x_best.append(xi_best)
            f_best.append(fi_best)
        else:
            x_best.append(x_best[-1])
            f_best.append(f_best[-1])
    return x_best, f_best  # return the best solution and fitness in each generation

#### Check Your Implementation: Running The Evolutionary Algorithm

Run the cell below, if you implemented everything correctly, you should see the algorithm running. Furthermore,

In [12]:
# Dummy parameters, please add or remove based on your implementation
kwargs = {
    "population_size": 20,
    "max_fit_evals": 5000,  # maximum number of fitness evaluations
    "p_crossover": 0.9,  # crossover probability
    "m_rate": 0.1,  # mutation rate
    "objective_function": cartpole,
}
# Run your algorithm once and find the best ANN weigths found
env = gym.make("CartPole-v1")
x_best, f_best = ea(**kwargs)


# Print the best ANN weigths found and best fitness
print("Best ANN parameters found:",x_best[-1])
print("Best fitnes found:",f_best[-1])


# Evaluate your ANN weights again and record the video
if f_best[-1] >= 1000:
  cartpole_record_video(x_best[-1] )
  #or cartpole_visualize(x_best[-1] )
else:
  print("The best fitness 1000 was not found, try again!!")

Step: 1, Observation: [ 0.01323574  0.17272775 -0.04686959 -0.3551522 ], Action: 1, Reward: 1.0, Total Reward: 1.0
Step: 2, Observation: [ 0.0166903   0.3684837  -0.05397264 -0.66223824], Action: 1, Reward: 1.0, Total Reward: 2.0
Step: 3, Observation: [ 0.02405997  0.5643134  -0.0672174  -0.97141534], Action: 1, Reward: 1.0, Total Reward: 3.0
Step: 4, Observation: [ 0.03534624  0.76026994 -0.08664571 -1.2844334 ], Action: 1, Reward: 1.0, Total Reward: 4.0
Step: 5, Observation: [ 0.05055164  0.95638156 -0.11233438 -1.6029392 ], Action: 1, Reward: 1.0, Total Reward: 5.0
Step: 6, Observation: [ 0.06967927  1.1526395  -0.14439316 -1.9284277 ], Action: 1, Reward: 1.0, Total Reward: 6.0
Step: 7, Observation: [ 0.09273206  1.3489841  -0.18296172 -2.262184  ], Action: 1, Reward: 1.0, Total Reward: 7.0
Step: 8, Observation: [ 0.11971174  1.545288   -0.2282054  -2.605216  ], Action: 1, Reward: 1.0, Total Reward: 8.0
Step: 1, Observation: [ 0.01323574  0.17272775 -0.04686959 -0.3551522 ], Action:

Step: 1, Observation: [ 0.01323574  0.17272775 -0.04686959 -0.3551522 ], Action: 1, Reward: 1.0, Total Reward: 1.0
Step: 2, Observation: [ 0.0166903   0.3684837  -0.05397264 -0.66223824], Action: 1, Reward: 1.0, Total Reward: 2.0
Step: 3, Observation: [ 0.02405997  0.5643134  -0.0672174  -0.97141534], Action: 1, Reward: 1.0, Total Reward: 3.0
Step: 4, Observation: [ 0.03534624  0.76026994 -0.08664571 -1.2844334 ], Action: 1, Reward: 1.0, Total Reward: 4.0
Step: 5, Observation: [ 0.05055164  0.95638156 -0.11233438 -1.6029392 ], Action: 1, Reward: 1.0, Total Reward: 5.0
Step: 6, Observation: [ 0.06967927  1.1526395  -0.14439316 -1.9284277 ], Action: 1, Reward: 1.0, Total Reward: 6.0
Step: 7, Observation: [ 0.09273206  1.3489841  -0.18296172 -2.262184  ], Action: 1, Reward: 1.0, Total Reward: 7.0
Step: 8, Observation: [ 0.11971174  1.545288   -0.2282054  -2.605216  ], Action: 1, Reward: 1.0, Total Reward: 8.0
Step: 1, Observation: [ 0.01323574  0.17272775 -0.04686959 -0.3551522 ], Action:

---
**Question 3 (0-0.25-0.5 pt):** Please comment on the behavior of the final solution. Were you able to find the best solution (i.e. ANN weights which achieves best fitness: 1000) and was it possible to controll the CartPole task without letting the the pole fall?

**Answer:** PLEASE FILL IN

**Average results of your algorithm**

Remember that the EAs are sthocastic algorithms that can produce different results as a result of independent runs.

Therefore, we would like to see the average results and standard deviations.


---
**Task 2 (0-1.5-3 pt):** Please run your algorithm for at least 10 times and plot the average results and standard deviations. Below, you may add as many cells as you need for this implementation and plot functions. You may use previous code you have developed/used during the course.

---
**Question 4 (0-0.25-0.5 pt):** Please comment on the average behavior of your algorithm. How did the average results and standard deviations look? Did your algorithm converge all the time to the best fitness?

**Answer:** PLEASE FILL IN